## Dependencies

In [1]:
# Import Splinter and BeautifulSoup
from splinter import Browser
from bs4 import BeautifulSoup as soup
from webdriver_manager.chrome import ChromeDriverManager
from selenium import webdriver
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.common.by import By
from selenium.common.exceptions import TimeoutException, NoSuchElementException
import time
import pandas as pd

In [2]:
executable_path = {'executable_path': ChromeDriverManager().install()}
browser = Browser('chrome', **executable_path, headless=False)



====== WebDriver manager ======
Current google-chrome version is 101.0.4951
Get LATEST chromedriver version for 101.0.4951 google-chrome
Trying to download new driver from https://chromedriver.storage.googleapis.com/101.0.4951.41/chromedriver_win32.zip
Driver has been saved in cache [C:\Users\drewa\.wdm\drivers\chromedriver\win32\101.0.4951.41]


## Cancer Incidence Data

In [3]:
# Visit the State Cancer Profile(Incidence) site
url = 'https://www.statecancerprofiles.cancer.gov/incidencerates/index.php'
browser.visit(url)
# Optional delay for loading the page
browser.is_element_present_by_css('div.col-xs-9', wait_time=1)

True

In [4]:
# Set the html parameter of interest
html = browser.html
can_soup = soup(html, 'html.parser')
slide_elem = can_soup.select_one('fieldset')

In [5]:
print(slide_elem.prettify())

<fieldset>
 <legend>
  Data Options
 </legend>
 <div class="inputWrap cf">
  <label for="stateFIPS">
   <strong>
    Area:
   </strong>
  </label>
  <select id="stateFIPS" name="stateFIPS" onchange="updateAreaType();">
   <option value="*">
    --- choose state ---
   </option>
   <option value="00">
    United States
   </option>
   <option value="01">
    Alabama
   </option>
   <option value="02">
    Alaska
   </option>
   <option value="04">
    Arizona
   </option>
   <option value="05">
    Arkansas
   </option>
   <option value="06">
    California
   </option>
   <option value="08">
    Colorado
   </option>
   <option value="09">
    Connecticut
   </option>
   <option value="10">
    Delaware
   </option>
   <option value="11">
    District of Columbia
   </option>
   <option value="12">
    Florida
   </option>
   <option value="13">
    Georgia
   </option>
   <option value="15">
    Hawaii
   </option>
   <option value="16">
    Idaho
   </option>
   <option value="17">
 

In [6]:
slide_elem.find_all('option')

[<option value="*">--- choose state ---</option>,
 <option value="00">United States</option>,
 <option value="01">Alabama</option>,
 <option value="02">Alaska </option>,
 <option value="04">Arizona</option>,
 <option value="05">Arkansas</option>,
 <option value="06">California</option>,
 <option value="08">Colorado</option>,
 <option value="09">Connecticut</option>,
 <option value="10">Delaware</option>,
 <option value="11">District of Columbia</option>,
 <option value="12">Florida</option>,
 <option value="13">Georgia</option>,
 <option value="15">Hawaii</option>,
 <option value="16">Idaho</option>,
 <option value="17">Illinois</option>,
 <option value="18">Indiana</option>,
 <option value="19">Iowa</option>,
 <option value="20">Kansas</option>,
 <option value="21">Kentucky</option>,
 <option value="22">Louisiana</option>,
 <option value="23">Maine</option>,
 <option value="24">Maryland</option>,
 <option value="25">Massachusetts</option>,
 <option value="26">Michigan</option>,
 <opti

In [7]:
# Cancer Incidence Data(2015-2019)

# Data options lists
#Area
state = {}
results = slide_elem.find_all('option')[2:54]
for result in results:
    state[result.attrs['value']] = result.text
state_keys = list(state)
# Cancer
cancer = {}
results = slide_elem.find_all('option')[59:81]
for result in results:
    cancer[result.attrs['value']] = result.text
cancer_keys = list(cancer)
# Race/Ethnicity
race = {}
results = slide_elem.find_all('option')[83:90]
for result in results:
    race[result.attrs['value']] = result.text
race_keys = list(race)
# Sex
sex = {}
results = slide_elem.find_all('option')[92:94]
for result in results:
    sex[result.attrs['value']] = result.text
sex_keys = list(sex)
# Age
age = {}
results = slide_elem.find_all('option')[96:100]
for result in results:
    age[result.attrs['value']] = result.text
age_keys = list(age)



In [8]:
# Reset dictionaries
cancer_reset = {'001':'All Cancer Sites'}
race_reset = {'00':'All Races (includes Hispanic)'}
sex_reset = {'0':'Both Sexes'}
age_reset = {'001':'All Ages'}

In [9]:
# site = f'https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS={state_num}&areatype=county&cancer={cancer_num}&race={race_num}&sex={sex_num}&age={age_num}&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results'

# For loop to change all data options to relevant data points

# Create empty dataframe
df = []

# Set initial parameters
cancer_num = list(cancer_reset.keys())[0]
race_num = list(race_reset.keys())[0]
sex_num = list(sex_reset.keys())[0]
age_num = list(age_reset.keys())[0]
print(cancer_num, race_num, sex_num, age_num)

001 00 0 001


In [10]:
race_inc_list = []
# Select Race features
cancer_num = list(cancer_reset.keys())[0]
sex_num = list(sex_reset.keys())[0]
age_num = list(age_reset.keys())[0]
for a in range(len(state_keys)):
    state_num = state_keys[a]
    for c in range(len(race_keys)):
        # URL variable
        race_num = race_keys[c]
        # Visit site
        url_to_visit = f'https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS={state_num}'
        url_to_visit += f'&areatype=county&cancer={cancer_num}'
        url_to_visit += f'&race={race_num}&sex={sex_num}'
        url_to_visit += f'&age={age_num}'
        url_to_visit += f'&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results'
        print("cancer_num", url_to_visit)
        
        browser.visit(url_to_visit)
        # Wait for load
        browser.is_element_present_by_css('div.col-xs-9', wait_time=4)
        url2 = f'https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS={state_num}'
        url2 += f'&areatype=county&cancer={cancer_num}'
        url2 += f'&race={race_num}&sex={sex_num}'
        url2 += f'&age={age_num}'
        url2 += f'&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results'
        print("url2", url2)
        y = pd.read_html(url2)[0]
        # Add selection criteria to y
        y.reindex(columns = y.columns.tolist() + ["State", "Cancer", "Race/Ethnicity", "Sex", "Age"])
        y['State'] = state[state_keys[a]]
        y['Cancer'] = "All Cancer Sites"
        y['Race/Ethnicity'] = race[race_keys[c]]
        y['Sex'] = "All Sexes"
        y['Age'] = 'All Ages'
        # Add to current dataframe
        display(y)
        race_inc_list.append(y)
        # Reset conditionals
        cancer_num = list(cancer_reset.keys())[0]
        sex_num = list(sex_reset.keys())[0]
        age_num = list(age_reset.keys())[0]
#         browser.quit()
   

cancer_num https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=01&areatype=county&cancer=001&race=01&sex=0&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results
url2 https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=01&areatype=county&cancer=001&race=01&sex=0&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results


County Met Healthy People Objective of ***?  \
0           Alabama  6                                  ***   
1    US (SEER+NPCR)  1                                  ***   
2    Lowndes County  6                                  ***   
3   Crenshaw County  6                                  ***   
4     Greene County  6                                  ***   
..                 ...                                  ...   
64    DeKalb County  6                                  ***   
65  Cherokee County  6                                  ***   
66       Lee County  6                                  ***   
67      Hale County  6                                  ***   
68     Coosa County  6                                  ***   

   Age-Adjusted Incidence Rate†cases per 100,000(95% Confidence Interval)  \
0                                445.6 (442.7, 448.4)                       
1                                451.0 (450.7, 451.4)                       
2                                681.2 (563.5, 819.6)                       
3                                558.3 (502.4, 619.2)                       
4                                542.5 (409.4, 714.1)                       
..                                                ...                       
64                               390.6 (371.5, 410.5)                       
65                               382.9 (353.9, 413.9)                       
66                               373.5 (357.2, 390.3)                       
67                               363.5 (308.9, 426.4)                       
68                               338.1 (289.2, 394.2)                       

   CI*Rank&fork;(95% Confidence Interval)  Average Annual Count Recent Trend  \
0                                     NaN                 20208      falling   
1                                     NaN               1419027      falling   
2                                1 (1, 8)                    30       rising   
3                               2 (1, 19)                    80       rising   
4                               3 (1, 67)                    15       stable   
..                                    ...                   ...          ...   
64                            63 (49, 67)                   332      falling   
65                            64 (44, 67)                   144       stable   
66                            65 (58, 67)                   413       stable   
67                            66 (25, 67)                    35       stable   
68                            67 (50, 67)                    41       stable   

   Recent 5-Year Trend‡ in Incidence Rates(95% Confidence Interval)    State  \
0                                   -0.9 (-1.3, -0.4)                Alabama   
1                                   -0.9 (-1.1, -0.7)                Alabama   
2                                    11.7 (3.4, 20.7)                Alabama   
3                                      2.7 (1.2, 4.3)                Alabama   
4                                     1.5 (-1.8, 5.0)                Alabama   
..                                                ...                    ...   
64                                  -1.4 (-2.3, -0.5)                Alabama   
65                                   -0.6 (-1.8, 0.5)                Alabama   
66                                   -0.7 (-1.6, 0.1)                Alabama   
67                                   -0.8 (-3.6, 2.1)                Alabama   
68                                   -2.2 (-4.4, 0.2)                Alabama   

              Cancer             Race/Ethnicity        Sex       Age  
0   All Cancer Sites  White (includes Hispanic)  All Sexes  All Ages  
1   All Cancer Sites  White (includes Hispanic)  All Sexes  All Ages  
2   All Cancer Sites  White (includes Hispanic)  All Sexes  All Ages  
3   All Cancer Sites  White (includes Hispanic)  All Sexes  All Ages  
4   All Cancer Sites  White (includes Hispanic)  All Sexe

cancer_num https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=01&areatype=county&cancer=001&race=06&sex=0&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results
url2 https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=01&areatype=county&cancer=001&race=06&sex=0&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results


County Met Healthy People Objective of ***?  \
0             Alabama  6                                  ***   
1     US (SEER+NPCR) § 1                                  ***   
2      Chilton County  6                                  ***   
3       Coffee County  6                                  ***   
4       Shelby County  6                                  ***   
..                   ...                                  ...   
64  Tallapoosa County  6                                  ***   
65      Walker County  6                                  ***   
66  Washington County  6                                  ***   
67      Wilcox County  6                                  ***   
68     Winston County  6                                  ***   

   Age-Adjusted Incidence Rate†cases per 100,000(95% Confidence Interval)  \
0                                201.6 (187.1, 216.8)                       
1                                343.9 (343.0, 344.8)                       
2                                498.4 (260.4, 828.9)                       
3                                338.8 (198.0, 531.1)                       
4                                298.2 (228.7, 380.4)                       
..                                                ...                       
64                                                  *                       
65                                                  *                       
66                                                  *                       
67                                                  *                       
68                                                  *                       

   CI*Rank&fork;(95% Confidence Interval) Average Annual Count Recent Trend  \
0                                     NaN                  182       stable   
1                                     NaN               125085      falling   
2                               1 (1, 12)                    4            *   
3                               2 (1, 14)                    5            *   
4                               3 (1, 10)                   16       stable   
..                                    ...                  ...          ...   
64                                      *           3 or fewer            *   
65                                      *           3 or fewer            *   
66                                      *           3 or fewer            *   
67                                      *           3 or fewer            *   
68                                      *           3 or fewer            *   

   Recent 5-Year Trend‡ in Incidence Rates(95% Confidence Interval)    State  \
0                                    -0.3 (-1.7, 1.2)                Alabama   
1                                   -1.7 (-2.6, -0.7)                Alabama   
2                                                   *                Alabama   
3                                                   *                Alabama   
4                                     0.7 (-2.2, 3.7)                Alabama   
..                                                ...                    ...   
64                                                  *                Alabama   
65                                                  *                Alabama   
66                                                  *                Alabama   
67                                                  *                Alabama   
68                                                  *                Alabama   

              Cancer    Race/Ethnicity        Sex       Age  
0   All Cancer Sites    White Hispanic  All Sexes  All Ages  
1   All Cancer Sites    White Hispanic  All Sexes  All Ages  
2   All Cancer Sites    White Hispanic  All Sexes  All Ages  
3   All Cancer Sites    White Hispanic  All Sexes  All Ages  
4   All Cancer Sites    White Hispanic  All Sexes  All Ages  
..               ...          

cancer_num https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=01&areatype=county&cancer=001&race=07&sex=0&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results
url2 https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=01&areatype=county&cancer=001&race=07&sex=0&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results


...

County Met Healthy People Objective of ***?  \
0              Wyoming  6                                  ***   
1       US (SEER+NPCR)  1                                  ***   
2       Fremont County  6                                  ***   
3        Albany County  6                                  ***   
4      Big Horn County  6                                  ***   
5      Campbell County  6                                  ***   
6        Carbon County  6                                  ***   
7      Converse County  6                                  ***   
8         Crook County  6                                  ***   
9        Goshen County  6                                  ***   
10  Hot Springs County  6                                  ***   
11      Johnson County  6                                  ***   
12      Laramie County  6                                  ***   
13      Lincoln County  6                                  ***   
14      Natrona County  6                                  ***   
15     Niobrara County  6                                  ***   
16         Park County  6                                  ***   
17       Platte County  6                                  ***   
18     Sheridan County  6                                  ***   
19     Sublette County  6                                  ***   
20   Sweetwater County  6                                  ***   
21        Teton County  6                                  ***   
22        Uinta County  6                                  ***   
23     Washakie County  6                                  ***   
24       Weston County  6                                  ***   

   Age-Adjusted Incidence Rate†cases per 100,000(95% Confidence Interval)  \
0                                423.5 (369.0, 483.3)                       
1                                285.8 (283.2, 288.4)                       
2                                505.4 (423.2, 598.1)                       
3                                                   *                       
4                                                   *                       
5                                                   *                       
6                                                   *                       
7                                                   *                       
8                                                   *                       
9                                                   *                       
10                                                  *                       
11                                                  *                       
12                                                  *                       
13                                                  *                       
14                                                  *                       
15                                                  *                       
16                                                  *                       
17                                                  *                       
18                                                  *                       
19                                                  *                       
20                                                  *                       
21                                                  *                       
22                                                  *                       
23                                                  *                       
24                                                  *                       

   CI*Rank&fork;(95% Confidence Interval) Average Annual Count Recent Trend  \
0                                     NaN                   51       stable   
1                                     NaN                10326      falling   
2                                     NaN                   31

cancer_num https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=56&areatype=county&cancer=001&race=04&sex=0&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results
url2 https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=56&areatype=county&cancer=001&race=04&sex=0&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results


County Met Healthy People Objective of ***?  \
0              Wyoming  6                                  ***   
1       US (SEER+NPCR)  1                                  ***   
2       Laramie County  6                                  ***   
3        Albany County  6                                  ***   
4      Big Horn County  6                                  ***   
5      Campbell County  6                                  ***   
6        Carbon County  6                                  ***   
7      Converse County  6                                  ***   
8         Crook County  6                                  ***   
9       Fremont County  6                                  ***   
10       Goshen County  6                                  ***   
11  Hot Springs County  6                                  ***   
12      Johnson County  6                                  ***   
13      Lincoln County  6                                  ***   
14      Natrona County  6                                  ***   
15     Niobrara County  6                                  ***   
16         Park County  6                                  ***   
17       Platte County  6                                  ***   
18     Sheridan County  6                                  ***   
19     Sublette County  6                                  ***   
20   Sweetwater County  6                                  ***   
21        Teton County  6                                  ***   
22        Uinta County  6                                  ***   
23     Washakie County  6                                  ***   
24       Weston County  6                                  ***   

   Age-Adjusted Incidence Rate†cases per 100,000(95% Confidence Interval)  \
0                                284.0 (218.0, 362.5)                       
1                                291.1 (290.0, 292.2)                       
2                                458.7 (289.0, 684.5)                       
3                                                   *                       
4                                                   *                       
5                                                   *                       
6                                                   *                       
7                                                   *                       
8                                                   *                       
9                                                   *                       
10                                                  *                       
11                                                  *                       
12                                                  *                       
13                                                  *                       
14                                                  *                       
15                                                  *                       
16                                                  *                       
17                                                  *                       
18                                                  *                       
19                                                  *                       
20                                                  *                       
21                                                  *                       
22                                                  *                       
23                                                  *                       
24                                                  *                       

   CI*Rank&fork;(95% Confidence Interval) Average Annual Count Recent Trend  \
0                                     NaN                   14            *   
1                                     NaN                56991      falling   
2                                     NaN                    5

cancer_num https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=56&areatype=county&cancer=001&race=05&sex=0&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results
url2 https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=56&areatype=county&cancer=001&race=05&sex=0&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results


County Met Healthy People Objective of ***?  \
0              Wyoming  6                                  ***   
1      US (SEER+NPCR) § 1                                  ***   
2    Sweetwater County  6                                  ***   
3       Laramie County  6                                  ***   
4        Goshen County  6                                  ***   
5        Albany County  6                                  ***   
6        Carbon County  6                                  ***   
7          Park County  6                                  ***   
8       Natrona County  6                                  ***   
9         Uinta County  6                                  ***   
10        Teton County  6                                  ***   
11      Fremont County  6                                  ***   
12     Campbell County  6                                  ***   
13     Big Horn County  6                                  ***   
14     Converse County  6                                  ***   
15        Crook County  6                                  ***   
16  Hot Springs County  6                                  ***   
17      Johnson County  6                                  ***   
18      Lincoln County  6                                  ***   
19     Niobrara County  6                                  ***   
20       Platte County  6                                  ***   
21     Sheridan County  6                                  ***   
22     Sublette County  6                                  ***   
23     Washakie County  6                                  ***   
24       Weston County  6                                  ***   

   Age-Adjusted Incidence Rate†cases per 100,000(95% Confidence Interval)  \
0                                330.8 (303.7, 359.5)                       
1                                345.0 (344.2, 345.9)                       
2                                429.1 (334.8, 539.7)                       
3                                384.9 (332.3, 443.1)                       
4                                381.9 (237.0, 579.9)                       
5                                381.1 (270.1, 519.2)                       
6                                365.7 (253.6, 507.2)                       
7                                322.3 (190.6, 505.5)                       
8                                321.7 (242.3, 416.7)                       
9                                310.0 (168.6, 525.3)                       
10                               298.1 (148.4, 516.5)                       
11                               251.8 (146.2, 397.9)                       
12                                191.8 (85.6, 358.3)                       
13                                                  *                       
14                                                  *                       
15                                                  *                       
16                                                  *                       
17                                                  *                       
18                                                  *                       
19                                                  *                       
20                                                  *                       
21                                                  *                       
22                                                  *                       
23                                                  *                       
24                                                  *                       

   CI*Rank&fork;(95% Confidence Interval) Average Annual Count Recent Trend  \
0                                     NaN                  123      falling   
1                                     NaN               137386      falling   
2                                1 (1, 7)                   18

In [11]:
race_inc_df = pd.concat(race_inc_list)
race_inc_df

County Met Healthy People Objective of ***?  \
0           Alabama  6                                  ***   
1    US (SEER+NPCR)  1                                  ***   
2    Lowndes County  6                                  ***   
3   Crenshaw County  6                                  ***   
4     Greene County  6                                  ***   
..                 ...                                  ...   
20    Platte County  6                                  ***   
21  Sheridan County  6                                  ***   
22  Sublette County  6                                  ***   
23  Washakie County  6                                  ***   
24    Weston County  6                                  ***   

   Age-Adjusted Incidence Rate†cases per 100,000(95% Confidence Interval)  \
0                                445.6 (442.7, 448.4)                       
1                                451.0 (450.7, 451.4)                       
2                                681.2 (563.5, 819.6)                       
3                                558.3 (502.4, 619.2)                       
4                                542.5 (409.4, 714.1)                       
..                                                ...                       
20                                                  *                       
21                                                  *                       
22                                                  *                       
23                                                  *                       
24                                                  *                       

   CI*Rank&fork;(95% Confidence Interval) Average Annual Count Recent Trend  \
0                                     NaN                20208      falling   
1                                     NaN              1419027      falling   
2                                1 (1, 8)                   30       rising   
3                               2 (1, 19)                   80       rising   
4                               3 (1, 67)                   15       stable   
..                                    ...                  ...          ...   
20                                      *           3 or fewer            *   
21                                      *           3 or fewer            *   
22                                      *           3 or fewer            *   
23                                      *           3 or fewer            *   
24                                      *           3 or fewer            *   

   Recent 5-Year Trend‡ in Incidence Rates(95% Confidence Interval)    State  \
0                                   -0.9 (-1.3, -0.4)                Alabama   
1                                   -0.9 (-1.1, -0.7)                Alabama   
2                                    11.7 (3.4, 20.7)                Alabama   
3                                      2.7 (1.2, 4.3)                Alabama   
4                                     1.5 (-1.8, 5.0)                Alabama   
..                                                ...                    ...   
20                                                  *                Wyoming   
21                                                  *                Wyoming   
22                                                  *                Wyoming   
23                                                  *                Wyoming   
24                                                  *                Wyoming   

              Cancer             Race/Ethnicity        Sex       Age Area  \
0   All Cancer Sites  White (includes Hispanic)  All Sexes  All Ages  NaN   
1   All Cancer Sites  White (includes Hispanic)  All Sexes  All Ages  NaN   
2   All Cancer Sites  White (includes Hispanic)  All Sexes  All Ages  NaN   
3   All Cancer Sites  White (includes Hispanic)  All Sexes  All Ages  NaN   
4   All Cancer Sites  White (includes H

In [12]:
race_inc_df.to_csv("race_inc_unlean.csv")

In [14]:
browser.quit()

In [13]:
race_inc_df1 =race_inc_df.drop("Met Healthy People Objective of ***?", axis='columns')
race_inc_df2 = race_inc_df1.drop("Area", axis='columns')
race_inc_df3 = race_inc_df2.drop("Parish", axis='columns')
race_inc_df3

County  \
0           Alabama  6   
1    US (SEER+NPCR)  1   
2    Lowndes County  6   
3   Crenshaw County  6   
4     Greene County  6   
..                 ...   
20    Platte County  6   
21  Sheridan County  6   
22  Sublette County  6   
23  Washakie County  6   
24    Weston County  6   

   Age-Adjusted Incidence Rate†cases per 100,000(95% Confidence Interval)  \
0                                445.6 (442.7, 448.4)                       
1                                451.0 (450.7, 451.4)                       
2                                681.2 (563.5, 819.6)                       
3                                558.3 (502.4, 619.2)                       
4                                542.5 (409.4, 714.1)                       
..                                                ...                       
20                                                  *                       
21                                                  *                       
22                                                  *                       
23                                                  *                       
24                                                  *                       

   CI*Rank&fork;(95% Confidence Interval) Average Annual Count Recent Trend  \
0                                     NaN                20208      falling   
1                                     NaN              1419027      falling   
2                                1 (1, 8)                   30       rising   
3                               2 (1, 19)                   80       rising   
4                               3 (1, 67)                   15       stable   
..                                    ...                  ...          ...   
20                                      *           3 or fewer            *   
21                                      *           3 or fewer            *   
22                                      *           3 or fewer            *   
23                                      *           3 or fewer            *   
24                                      *           3 or fewer            *   

   Recent 5-Year Trend‡ in Incidence Rates(95% Confidence Interval)    State  \
0                                   -0.9 (-1.3, -0.4)                Alabama   
1                                   -0.9 (-1.1, -0.7)                Alabama   
2                                    11.7 (3.4, 20.7)                Alabama   
3                                      2.7 (1.2, 4.3)                Alabama   
4                                     1.5 (-1.8, 5.0)                Alabama   
..                                                ...                    ...   
20                                                  *                Wyoming   
21                                                  *                Wyoming   
22                                                  *                Wyoming   
23                                                  *                Wyoming   
24                                                  *                Wyoming   

              Cancer             Race/Ethnicity        Sex       Age  
0   All Cancer Sites  White (includes Hispanic)  All Sexes  All Ages  
1   All Cancer Sites  White (includes Hispanic)  All Sexes  All Ages  
2   All Cancer Sites  White (includes Hispanic)  All Sexes  All Ages  
3   All Cancer Sites  White (includes Hispanic)  All Sexes  All Ages  
4   All Cancer Sites  White (includes Hispanic)  All Sexes  All Ages  
..               ...                        ...        ...       ...  
20  All Cancer Sites        Hispanic (any race)  All Sexes  All Ages  
21  All Cancer Sites        Hispanic (any race)  All Sexes  All Ages  
22  All Cancer Sites        Hispanic (any race)  All Sexes  All Ages  
23  All Cancer Sites        Hispanic (any race)  All Sexes  All Ages  
24  All Cancer Sites        Hispanic (any race)  All Sexes  All Ages  

[22701 rows x 1

In [ ]:
race_inc_df4 = race_inc_df3.dropna()
race_inc_df4['Age-Adjusted Incidence Rate cases per 100,000'] = race_inc_df4['Age-Adjusted Incidence Rate†cases per 100,000(95% Confidence Interval)'].str.replace(r'\(.*\)', '')
race_inc_df4['CI*Rank'] = race_inc_df4['CI*Rank&fork;(95% Confidence Interval)'].str.replace(r'\(.*\)', '')
race_inc_df4['Recent 5-Year Trend in Incidence Rates'] = race_inc_df4['Recent 5-Year Trend‡ in Incidence Rates(95% Confidence Interval)'].str.replace(r'\(.*\)', '')
race_inc_df5 = race_inc_df4.drop(["Age-Adjusted Incidence Rate†cases per 100,000(95% Confidence Interval)",'CI*Rank&fork;(95% Confidence Interval)', 'Recent 5-Year Trend‡ in Incidence Rates(95% Confidence Interval)'], axis='columns')
race_inc_df5.head(70)

In [52]:
race_inc_df5.to_csv('race_inc.csv')

In [34]:
sex_inc_list = []
# Select Sex features
cancer_num = list(cancer_reset.keys())[0]
race_num = list(race_reset.keys())[0]
sex_num = list(sex_reset.keys())[0]
age_num = list(age_reset.keys())[0]
for a in range(len(state_keys)):
    state_num = state_keys[a]
    for d in range(len(sex_keys)):
        # URL variable
        sex_num = sex_keys[d]
        # Visit site
        url_to_visit = f'https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS={state_num}'
        url_to_visit += f'&areatype=county&cancer={cancer_num}'
        url_to_visit += f'&race={race_num}&sex={sex_num}'
        url_to_visit += f'&age={age_num}'
        url_to_visit += f'&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results'
        print("cancer_num", url_to_visit)
        
        browser.visit(url_to_visit)
        # Wait for load
        browser.is_element_present_by_css('div.col-xs-9', wait_time=4)
        url2 = f'https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS={state_num}'
        url2 += f'&areatype=county&cancer={cancer_num}'
        url2 += f'&race={race_num}&sex={sex_num}'
        url2 += f'&age={age_num}'
        url2 += f'&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results'
        print("url2", url2)
        y = pd.read_html(url2)[0]
        # Add selection criteria to y
        y.reindex(columns = y.columns.tolist() + ["State", "Cancer", "Race/Ethnicity", "Sex", "Age"])
        y['State'] = state[state_keys[a]]
        y['Cancer'] = "All Cancer Sites"
        y['Race/Ethnicity'] = "All Races (includes Hispanic)"
        y['Sex'] = sex[sex_keys[d]]
        y['Age'] = 'All Ages'
        # Add to current dataframe
        display(y)
        sex_inc_list.append(y)
        # Reset conditionals
        cancer_num = list(cancer_reset.keys())[0]
        sex_num = list(sex_reset.keys())[0]
        age_num = list(age_reset.keys())[0]
#         browser.quit()
  

cancer_num https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=01&areatype=county&cancer=001&race=00&sex=1&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results
url2 https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=01&areatype=county&cancer=001&race=00&sex=1&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results


County Met Healthy People Objective of ***?  \
0           Alabama  6                                  ***   
1    US (SEER+NPCR)  1                                  ***   
2    Lowndes County  6                                  ***   
3   Chambers County  6                                  ***   
4     Elmore County  6                                  ***   
..                 ...                                  ...   
64      Hale County  6                                  ***   
65       Lee County  6                                  ***   
66  Cherokee County  6                                  ***   
67    DeKalb County  6                                  ***   
68     Coosa County  6                                  ***   

   Age-Adjusted Incidence Rate†cases per 100,000(95% Confidence Interval)  \
0                                515.2 (511.3, 519.1)                       
1                                487.4 (486.9, 487.8)                       
2                                730.1 (635.8, 835.5)                       
3                                607.4 (559.4, 658.6)                       
4                                591.1 (557.8, 625.9)                       
..                                                ...                       
64                               454.8 (393.4, 523.8)                       
65                               453.8 (430.2, 478.3)                       
66                               425.2 (383.2, 471.2)                       
67                               419.8 (391.7, 449.4)                       
68                               389.8 (328.5, 460.7)                       

   CI*Rank&fork;(95% Confidence Interval)  Average Annual Count Recent Trend  \
0                                     NaN                 14158       stable   
1                                     NaN                859984      falling   
2                                1 (1, 7)                    47       stable   
3                               2 (1, 25)                   129       stable   
4                               3 (2, 20)                   256       stable   
..                                    ...                   ...          ...   
64                            63 (12, 67)                    44      falling   
65                            64 (46, 66)                   304       stable   
66                            65 (44, 67)                    84      falling   
67                            66 (56, 67)                   176      falling   
68                            67 (47, 67)                    32      falling   

   Recent 5-Year Trend‡ in Incidence Rates(95% Confidence Interval)    State  \
0                                    -0.2 (-1.3, 0.9)                Alabama   
1                                   -1.1 (-1.7, -0.5)                Alabama   
2                                     1.9 (-0.6, 4.5)                Alabama   
3                                     0.0 (-1.0, 1.0)                Alabama   
4                                     0.3 (-0.6, 1.2)                Alabama   
..                                                ...                    ...   
64                                 -5.8 (-10.1, -1.3)                Alabama   
65                                   -0.8 (-1.7, 0.2)                Alabama   
66                                  -1.6 (-2.9, -0.3)                Alabama   
67                                  -2.9 (-4.1, -1.7)                Alabama   
68                                  -2.4 (-4.4, -0.2)                Alabama   

              Cancer                 Race/Ethnicity    Sex       Age  
0   All Cancer Sites  All Races (includes Hispanic)  Males  All Ages  
1   All Cancer Sites  All Races (includes Hispanic)  Males  All Ages  
2   All Cancer Sites  All Races (includes Hispanic)  Males  All Ages  
3   All Cancer Sites  All Races (includes Hispanic)  Males  All Ages  
4   All Cancer Sites  All Races (includes Hispanic)  Male

cancer_num https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=01&areatype=county&cancer=001&race=00&sex=2&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results
url2 https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=01&areatype=county&cancer=001&race=00&sex=2&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results


County Met Healthy People Objective of ***?  \
0           Alabama  6                                  ***   
1    US (SEER+NPCR)  1                                  ***   
2    Lowndes County  6                                  ***   
3    Pickens County  6                                  ***   
4   Crenshaw County  6                                  ***   
..                 ...                                  ...   
64  Cherokee County  6                                  ***   
65       Lee County  6                                  ***   
66     Coosa County  6                                  ***   
67   Winston County  6                                  ***   
68      Hale County  6                                  ***   

   Age-Adjusted Incidence Rate†cases per 100,000(95% Confidence Interval)  \
0                                404.1 (400.9, 407.4)                       
1                                422.7 (422.3, 423.2)                       
2                                504.8 (428.3, 591.6)                       
3                                504.8 (450.0, 564.8)                       
4                                497.5 (433.4, 569.2)                       
..                                                ...                       
64                               352.5 (313.7, 395.4)                       
65                               331.2 (313.2, 350.1)                       
66                               331.2 (274.0, 398.3)                       
67                               326.8 (286.7, 371.4)                       
68                               324.6 (276.0, 379.9)                       

   CI*Rank&fork;(95% Confidence Interval)  Average Annual Count Recent Trend  \
0                                     NaN                 12742       rising   
1                                     NaN                843265       stable   
2                               1 (1, 45)                    35       rising   
3                               2 (1, 28)                    68       rising   
4                               3 (1, 39)                    48       rising   
..                                    ...                   ...          ...   
64                            63 (25, 67)                    68       stable   
65                            64 (58, 67)                   262      falling   
66                            65 (15, 67)                    27       stable   
67                            66 (37, 67)                    55       stable   
68                            67 (25, 67)                    35       stable   

   Recent 5-Year Trend‡ in Incidence Rates(95% Confidence Interval)    State  \
0                                      0.4 (0.1, 0.6)                Alabama   
1                                    -0.8 (-1.6, 0.1)                Alabama   
2                                      2.2 (0.5, 3.9)                Alabama   
3                                      3.1 (1.1, 5.1)                Alabama   
4                                      3.4 (1.6, 5.3)                Alabama   
..                                                ...                    ...   
64                                    0.1 (-1.9, 2.2)                Alabama   
65                                  -3.7 (-5.9, -1.4)                Alabama   
66                                    0.1 (-2.7, 3.1)                Alabama   
67                                   -1.5 (-3.1, 0.1)                Alabama   
68                                   -0.3 (-2.5, 2.0)                Alabama   

              Cancer                 Race/Ethnicity      Sex       Age  
0   All Cancer Sites  All Races (includes Hispanic)  Females  All Ages  
1   All Cancer Sites  All Races (includes Hispanic)  Females  All Ages  
2   All Cancer Sites  All Races (includes Hispanic)  Females  All Ages  
3   All Cancer Sites  All Races (includes Hispanic)  Females  All Ages  
4   All Cancer Sites  All Races (includes Hispa

cancer_num https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=02&areatype=county&cancer=001&race=00&sex=1&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results
url2 https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=02&areatype=county&cancer=001&race=00&sex=1&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results


...

County Met Healthy People Objective of ***?  \
0             Arizona  6                                  ***   
1      US (SEER+NPCR)  1                                  ***   
2     Greenlee County  6                                  ***   
3       Mohave County  6                                  ***   
4      Yavapai County  6                                  ***   
5       Graham County  6                                  ***   
6     Maricopa County  6                                  ***   
7         Pima County  6                                  ***   
8      Cochise County  6                                  ***   
9         Yuma County  6                                  ***   
10    Coconino County  6                                  ***   
11       Pinal County  6                                  ***   
12        Gila County  6                                  ***   
13      Navajo County  6                                  ***   
14  Santa Cruz County  6                                  ***   
15      La Paz County  6                                  ***   
16      Apache County  6                                  ***   

   Age-Adjusted Incidence Rate†cases per 100,000(95% Confidence Interval)  \
0                                368.5 (365.8, 371.1)                       
1                                422.7 (422.3, 423.2)                       
2                                399.5 (320.7, 491.5)                       
3                                392.3 (377.3, 407.7)                       
4                                384.3 (370.3, 398.7)                       
5                                381.4 (342.5, 423.6)                       
6                                376.7 (373.2, 380.2)                       
7                                370.5 (363.7, 377.4)                       
8                                354.8 (336.2, 374.3)                       
9                                345.2 (329.9, 361.0)                       
10                               345.1 (325.0, 366.1)                       
11                               335.9 (325.4, 346.6)                       
12                               325.9 (298.9, 355.0)                       
13                               310.9 (291.4, 331.4)                       
14                               308.7 (280.2, 339.4)                       
15                               299.7 (255.4, 350.0)                       
16                               260.6 (237.9, 285.0)                       

   CI*Rank&fork;(95% Confidence Interval)  Average Annual Count Recent Trend  \
0                                     NaN                 15876      falling   
1                                     NaN                843265       stable   
2                               1 (1, 13)                    19       stable   
3                                2 (1, 5)                   696       stable   
4                                3 (1, 6)                   793       stable   
5                               4 (1, 10)                    74       stable   
6                                5 (2, 6)                  9272      falling   
7                                6 (3, 7)                  2545      falling   
8                               7 (4, 11)                   315       stable   
9                               8 (6, 12)                   421       rising   
10                              9 (5, 12)                   238       stable   
11                             10 (7, 12)                   888      falling   
12                             11 (6, 14)                   145       stable   
13                            12 (10, 14)                   209       stable   
14                             13 (8, 14)                    92       stable   
15                             14 (7, 15)                    52       stable   
16                            15 (14, 15)                   105       stable   

   Recent 5-Year Tr

cancer_num https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=05&areatype=county&cancer=001&race=00&sex=1&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results
url2 https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=05&areatype=county&cancer=001&race=00&sex=1&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results


County Met Healthy People Objective of ***?  \
0           Arkansas  6                                  ***   
1     US (SEER+NPCR)  1                                  ***   
2    Woodruff County  6                                  ***   
3   Cleveland County  6                                  ***   
4      Monroe County  6                                  ***   
..                  ...                                  ...   
72      Izard County  6                                  ***   
73  Lafayette County  6                                  ***   
74     Howard County  6                                  ***   
75     Sevier County  6                                  ***   
76     Newton County  6                                  ***   

   Age-Adjusted Incidence Rate†cases per 100,000(95% Confidence Interval)  \
0                                543.5 (538.4, 548.6)                       
1                                487.4 (486.9, 487.8)                       
2                                711.1 (598.9, 839.9)                       
3                                707.0 (609.8, 816.9)                       
4                                691.7 (589.4, 808.7)                       
..                                                ...                       
72                               432.9 (379.2, 493.5)                       
73                               429.5 (350.3, 523.8)                       
74                               420.2 (357.3, 491.5)                       
75                               394.1 (337.0, 458.2)                       
76                               365.4 (297.1, 447.0)                       

   CI*Rank&fork;(95% Confidence Interval)  Average Annual Count Recent Trend  \
0                                     NaN                  9292       stable   
1                                     NaN                859984      falling   
2                               1 (1, 40)                    32       stable   
3                               2 (1, 35)                    40       stable   
4                               3 (1, 39)                    35       stable   
..                                    ...                   ...          ...   
72                            71 (41, 75)                    50      falling   
73                            72 (25, 75)                    23       stable   
74                            73 (40, 75)                    34      falling   
75                            74 (56, 75)                    35       stable   
76                            75 (55, 75)                    24       stable   

   Recent 5-Year Trend‡ in Incidence Rates(95% Confidence Interval)     State  \
0                                     0.6 (-0.4, 1.6)                Arkansas   
1                                   -1.1 (-1.7, -0.5)                Arkansas   
2                                     0.4 (-1.3, 2.1)                Arkansas   
3                                   12.8 (-0.9, 28.5)                Arkansas   
4                                     0.0 (-1.6, 1.7)                Arkansas   
..                                                ...                     ...   
72                                  -2.0 (-3.3, -0.8)                Arkansas   
73                                   -0.4 (-2.4, 1.7)                Arkansas   
74                                  -2.8 (-4.8, -0.8)                Arkansas   
75                                   -1.3 (-3.5, 0.9)                Arkansas   
76                                   -1.7 (-3.8, 0.3)                Arkansas   

              Cancer                 Race/Ethnicity    Sex       Age  
0   All Cancer Sites  All Races (includes Hispanic)  Males  All Ages  
1   All Cancer Sites  All Races (includes Hispanic)  Males  All Ages  
2   All Cancer Sites  All Races (includes Hispanic)  Males  All Ages  
3   All Cancer Sites  All Races (includes Hispanic)  Males  All Ages  
4   All Cancer Sites  All Races (i

cancer_num https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS=05&areatype=county&cancer=001&race=00&sex=2&age=001&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results



KeyboardInterrupt



In [ ]:
sex_inc_df = pd.concat(sex_inc_list)
sex_inc_df

In [ ]:

age_inc_list = []
# Select Age features
cancer_num = list(cancer_reset.keys())[0]
race_num = list(race_reset.keys())[0]
sex_num = list(sex_reset.keys())[0]
age_num = list(age_reset.keys())[0]
for a in range(len(state_keys)):
    state_num = state_keys[a]
    for e in range(len(age_keys)):
        # URL variable
        age_num = age_keys[e]
        # Visit site
        url_to_visit = f'https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS={state_num}'
        url_to_visit += f'&areatype=county&cancer={cancer_num}'
        url_to_visit += f'&race={race_num}&sex={sex_num}'
        url_to_visit += f'&age={age_num}'
        url_to_visit += f'&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results'
        print("cancer_num", url_to_visit)
        
        browser.visit(url_to_visit)
        # Wait for load
        browser.is_element_present_by_css('div.col-xs-9', wait_time=4)
        url2 = f'https://www.statecancerprofiles.cancer.gov/incidencerates/index.php?stateFIPS={state_num}'
        url2 += f'&areatype=county&cancer={cancer_num}'
        url2 += f'&race={race_num}&sex={sex_num}'
        url2 += f'&age={age_num}'
        url2 += f'&stage=999&year=0&type=incd&sortVariableName=rate&sortOrder=default&output=0#results'
        print("url2", url2)
        y = pd.read_html(url2)[0]
        # Add selection criteria to y
        y.reindex(columns = y.columns.tolist() + ["State", "Cancer", "Race/Ethnicity", "Sex", "Age"])
        y['State'] = state[state_keys[a]]
        y['Cancer'] = "All Cancer Sites"
        y['Race/Ethnicity'] = "All Races (includes Hispanic)"
        y['Sex'] = "All Sexes"
        y['Age'] = age[age_keys[e]]
        # Add to current dataframe
        display(y)
        age_inc_list.append(y)
        # Reset conditionals
        cancer_num = list(cancer_reset.keys())[0]
        race_num = list(race_reset.keys())[0]
        sex_num = list(sex_reset.keys())[0]
        age_num = list(age_reset.keys())[0]

        

In [ ]:
age_inc_df = pd.concat(age_inc_list)
age_inc_df

In [53]:
# Save DataFrame as csv
browser.quit()